# Reinforcement Learning control strategies for Electric Vehicles fleet Virtual Power Plants
Thesis based on the development of a RL agent that manages a VPP through EVs charging stations in an household environment. Main optimization objectives of the VPP are: Valley filling, peak shaving and zero resulting load over time. Main action performed to reach objectives are: storage of Renewable energy resources and power push in the grid at high demand times. The development of the Virtual Power Plant environment is based on the ELVIS (Electric Vehicles Infrastructure Simulator) open library from DAI-Labor: https://github.com/dailab/elvis The thesis code is currently available at: (https://github.com/francescomaldonato/RL_VPP_Thesis)

Author: Francesco Maldonato

## VPP simulator Notebook based on EVs arrival, with StableBaselines3 trained model (Recurrent PPO) [30 EVs per week test]

Installing required packages and dependencies

In [1]:
%%capture
!pip install py-elvis==0.2.1
!pip install pyyaml==5.4
!pip install plotly==5.9.0
!pip install -U kaleido==0.2.1

!pip install stable-baselines3[extra]==1.6.1
!pip install stable-baselines==1.6.1
!pip install sb3-contrib==1.6.1
!pip install gym==0.20.0
!pip install -q wandb==0.13.4

In [3]:
#Cloning repository and changing directory
!git clone https://github.com/francescomaldonato/RL_VPP_Thesis.git
%cd RL_VPP_Thesis/
%ls

In [4]:
import yaml
import numpy as np
from gym import Env
from VPP_environment import VPPEnv, VPP_Scenario_config
from elvis.config import ScenarioConfig
import os
import torch
import random
import wandb
from sb3_contrib import RecurrentPPO #The available algoritmhs in sb3-contrib for the custom environment with MultiInputPolicy
from sb3_contrib.common.maskable.utils import get_action_masks
import stable_baselines3 as sb3
from stable_baselines3.common.env_checker import check_env

#Check if cuda device is available for training
print("Torch-Cuda available device:", torch.cuda.is_available())
print(sb3.get_system_info())
#!wandb --version

Torch-Cuda available device: False
OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022
Python: 3.7.15
Stable-Baselines3: 1.6.1
PyTorch: 1.12.1+cu113
GPU Enabled: False
Numpy: 1.21.6
Gym: 0.20.0

({'OS': 'Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022', 'Python': '3.7.15', 'Stable-Baselines3': '1.6.1', 'PyTorch': '1.12.1+cu113', 'GPU Enabled': 'False', 'Numpy': '1.21.6', 'Gym': '0.20.0'}, 'OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022\nPython: 3.7.15\nStable-Baselines3: 1.6.1\nPyTorch: 1.12.1+cu113\nGPU Enabled: False\nNumpy: 1.21.6\nGym: 0.20.0\n')


In [5]:
# Ensure deterministic behavior
torch.backends.cudnn.deterministic = True
random.seed(0)
torch.manual_seed(0)
torch.cuda.manual_seed_all(0)

## Load ELVIS YAML config file
Section where the EVs arrival simulation parameters are loaded through the Yaml config file from the 'data/config_builder/' folder.

In [6]:
#Loading paths for input data
current_folder = ''
VPP_training_data_input_path = current_folder + 'data/data_training/environment_table/' + 'Environment_data_2019.csv'
VPP_testing_data_input_path = current_folder + 'data/data_testing/environment_table/' + 'Environment_data_2020.csv'
VPP_validating_data_input_path = current_folder + 'data/data_validating/environment_table/' + 'Environment_data_2018.csv'
elvis_input_folder = current_folder + 'data/config_builder/'

#case = 'wohnblock_household_simulation_adaptive.yaml' #(loaded by default, 20 EVs arrivals per week with 50% average battery)

#Try different simulation parameters, uncomment below
#case = 'wohnblock_household_simulation_adaptive_10.yaml' #(10 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_15.yaml' #(15 EVs arrivals per week with 50% average battery)
#case = 'wohnblock_household_simulation_adaptive_25.yaml' #(25 EVs arrivals per week with 50% average battery) 
case = 'wohnblock_household_simulation_adaptive_30.yaml' #(30 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_35.yaml' #(35 EVs arrivals per week with 50% average battery) 

with open(elvis_input_folder + case, 'r') as file:
    yaml_str = yaml.full_load(file)

elvis_config_file = ScenarioConfig.from_yaml(yaml_str)
VPP_config_file = VPP_Scenario_config(yaml_str)

print(elvis_config_file)
print(VPP_config_file)

Vehicle types: <generator object ScenarioConfig.__str__.<locals>.<genexpr> at 0x7f5f7bf736d0>Mean parking time: 23.99
Std deviation of parking time: 1
Mean value of the SOC distribution: 0.5
Std deviation of the SOC distribution: 0.1
Max parking time: 24
Number of charging events per week: 30
Vehicles are disconnected only depending on their parking time
Queue length: 0
Opening hours: None
Scheduling policy: Uncontrolled

{'start_date': '2022-01-01T00:00:00', 'end_date': '2023-01-01T00:00:00', 'resolution': '0:15:00', 'num_households': 4, 'solar_power': 16, 'wind_power': 12, 'EV_types': [{'battery': {'capacity': 100, 'efficiency': 1, 'max_charge_power': 150, 'min_charge_power': 0}, 'brand': 'Tesla', 'model': 'Model S', 'probability': 1}], 'charging_stations_n': 4, 'EVs_n': 30, 'EVs_n_max': 1566, 'mean_park': 23.99, 'std_deviation_park': 1, 'EVs_mean_soc': 50.0, 'EVs_std_deviation_soc': 10.0, 'EV_load_max': 44, 'EV_load_rated': 14.8, 'EV_load_min': 1, 'houseRWload_max': 10, 'av_max_ener

In [7]:
#TESTING Environment initialization
env = VPPEnv(VPP_testing_data_input_path, elvis_config_file, VPP_config_file)
#env.plot_VPP_input_data()

Charging event: 1, Arrival time: 2022-01-01 05:00:00, Parking_time: 23.608193551093244, Leaving_time: 2022-01-02 04:36:29.496784, SOC: 0.39080188753318884, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 1565, Arrival time: 2022-12-31 21:15:00, Parking_time: 22.840745634008172, Leaving_time: 2023-01-01 20:05:26.684282, SOC: 0.5647102468473889, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -21214.64 , Grid_used_en(grid-import)=4947.18kWh , autarky-rate=83.0 , RE-to-vehicle_unused_en(grid-export)=-26161.81kWh , self-consump.rate=47.9 , Total_selling_cost=€  -489.75 , Grid_cost=€  233.11
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  30951.08 , Grid_used_en=kWh  46588.26 , RE-to-vehicle_unused_en=kWh  15637.18 , Total_selling_cost=€  1184.38 , Grid_cost=€  1641.68 , Charging_events=  1565 
- Exp.VPP_goals: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  66.72


In [8]:
env.plot_ELVIS_data()

In [9]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
env.plot_reward_functions()

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  31416.27 , Grid_used_en(grid-import)=46856.99kWh , Total_demand=81681.19kWh , autarky-rate=42.6 , RE-to-vehicle_unused_en(grid-export)=15440.72kWh , Total_supply=50264.92kWh , self-consump.rate=69.3 , Grid_cost=€  1616.9 , Total_selling_cost=€  1164.79 , Av.EV_en_left=kWh  100.0 , Charging_events=  1565 
- VPP_goal_upper_limit: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  66.72
Simulating VPP....


### VPP Simulation test with random actions [no model loaded]

In [10]:
episodes = 1
for episode in range(1, episodes+1):
    state = env.reset()
    done = False
    score = 0
    while not done:
        action_masks = get_action_masks(env)
        action = env.action_space.sample()
        
        n_state, reward, done, info = env.step(action)
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [11]:
env.plot_VPP_autarky()

In [12]:
#env.plot_Elvis_results()

In [13]:
#env.plot_VPP_results()

In [14]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [15]:
env.plot_VPP_Elvis_comparison()

In [16]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [17]:
env.plot_rewards_stats()

In [18]:
env.plot_EVs_kpi()

In [19]:
env.plot_actions_kpi()

In [20]:
env.plot_load_kpi()

In [21]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

In [22]:
## Wandb login to load models
#In Colab, uncomment below:
# %env "WANDB_DISABLE_CODE" True
# %env "WANDB_NOTEBOOK_NAME" "VPP_simulator.ipynb"
# os.environ['WANDB_NOTEBOOK_NAME'] = 'VPP_simulator.ipynb'
#wandb.login(relogin=True)

#In local notebook, uncomment below:
#your_wandb_login_code = 0123456789abcdefghijklmnopqrstwxyzàèìòù0 #example length
#!wandb login {your_wandb_login_code}

In [23]:
#Loading training model, from local directory or from wandb previous trainings
RecurrentPPO_path = "trained_models/RecurrentPPO_models/model_RecurrentPPO_"

#model_id = "s37o8q0n"
model_id = "333ckz0i"
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

# run_id_restore = "2y2dqvyn"
# model = wandb.restore(f'model_{run_id_restore}.zip', run_path=f"francesco_maldonato/RL_VPP_Thesis/{run_id_restore}")

/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


## Testing dataset VPP Simulation using the loaded trained model

In [24]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

#Save the VPP table
VPP_table = env.save_VPP_table(save_path='data/environment_optimized_output/VPP_table.csv')

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  32471.56 , Grid_used_en(grid-import)=48173.44kWh , Total_demand=82741.4kWh , autarky-rate=41.8 , RE-to-vehicle_unused_en(grid-export)=15701.88kWh , Total_supply=50269.84kWh , self-consump.rate=68.8 , Grid_cost=€  1676.17 , Total_selling_cost=€  1211.5 , Av.EV_en_left=kWh  100.0 , Charging_events=  1565 
- VPP_goal_upper_limit: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  66.72
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -1158.07 , Grid_used_en(grid-import)=1646.67kWh , Total_demand=64872.88kWh , autarky-rate=97.5 , RE-to-vehicle_unused_en(grid-export)=2804.74kWh , Total_supply=66030.95kWh , self-consump.rate=95.8 , Total_selling_cost=€  -7.55 , Grid_cost=€  63.83 
 EV_INFO: Av.EV_energy_leaving=kWh  62.34 , Std.EV_energy_leaving=kWh  24.11 , EV_departures =  1565 , EV_queue_left =  0
SCORE:  Cumulative_reward= 470030.07 - Step_rewars (load_t= 435014.46, EVs_ene

In [25]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [26]:
VPP_table.head(15000)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00  65.919121  59.885036  70.278481  51.187565   
2022-01-01 00:15:00  66.169121  59.317078  69.710518  51.437565   
2022-01-01 00:30:00  66.419121  58.769081  69.162521  51.687565   
2022-01-01 00:45:00  66.669121  58.276943  68.670387  51.937565   
2022-01-01 01:00:00  66.919121  57.826984  68.220428  52.187565   
...                        ...        ...        ...        ...   
2022-06-06 04:45:00  86.079559  38.208344  70.238937  59.262970   
2022-06-06 05:00:00  86.079559  37.958344  48.434036  60.757607   
2022-06-06 05:15:00  86.079559  38.931999  49.407692  61.731262   
2022-06-06 05:30:00  86.901115  39.753559  50.229252  62.552822   
2022-06-06 05:45:00  87.658867  40.511307  50.987000  63.310570   

                                       EVs_id       actions  \
time                                                          
2022-01-01 00:00:00              [0, 0, 0, 0]  [1, 2, 2, 1]   
2022-01-01 00:15:00  [4692, 4693, 4694, 4695]  [1, 2, 2, 1]   
2022-01-01 00:30:00  [4692, 4693, 4694, 4695]  [1, 2, 2, 1]   
2022-01-01 00:45:00  [4692, 4693, 4694, 4695]  [1, 2, 2, 1]   
2022-01-01 01:00:00  [4692, 4693, 4694, 4695]  [1, 2, 2, 1]   
...                                       ...           ...   
2022-06-06 04:45:00  [5370, 5369, 5368, 5371]  [0, 2, 1, 1]   
2022-06-06 05:00:00  [5370, 5369, 5372, 5371]  [0, 1, 1, 1]   
2022-06-06 05:15:00  [5370, 5369, 5372, 5371]  [1, 1, 1, 1]   
2022-06-06 05:30:00  [5370, 5369, 5372, 5371]  [1, 1, 1, 1]   
2022-06-06 05:45:00  [5370, 5369, 5372, 5371]  [1, 1, 1, 1]   

                                       mask_truth  ev_charged_pwr  \
time                                                                
2022-01-01 00:00:00  [False, False, False, False]        0.000000   
2022-01-01 00:15:00    [False, True, True, False]        2.000000   
2022-01-01 00:30:00    [False, True, True, False]        2.000000   
2022-01-01 00:45:00    [False, True, True, False]        2.000000   
2022-01-01 01:00:00    [False, True, True, False]        2.000000   
...                                           ...             ...   
2022-06-06 04:45:00     [True, False, True, True]        9.009417   
2022-06-06 05:00:00      [True, True, True, True]       11.957087   
2022-06-06 05:15:00      [True, True, True, True]       11.683883   
2022-06-06 05:30:00      [True, True, True, True]       13.144929   
2022-06-06 05:45:00      [True, True, True, True]       12.123966   

                     ev_discharged_pwr          load  load_reward  EV_reward  \
time                                                                           
2022-01-01 00:00:00           0.000000  2.124144e+00         15.0   0.000000   
2022-01-01 00:15:00          -4.543681  4.440892e-16         15.0   0.000000   
2022-01-01 00:30:00          -4.383959  4.440892e-16         15.0   0.000000   
2022-01-01 00:45:00          -3.937089  0.000000e+00         15.0   0.000000   
2022-01-01 01:00:00          -3.599678  2.220446e-16         15.0   0.000000   
...                                ...           ...          ...        ...   
2022-06-06 04:45:00          -1.000000  0.000000e+00         15.0  63.234473   
2022-06-06 05:00:00          -1.000000  0.000000e+00         15.0   0.000000   
2022-06-06 05:15:00           0.000000  0.000000e+00         15.0   0.000000   
2022-06-06 05:30:00           0.000000  0.000000e+00         15.0   0.000000   
2022-06-06 05:45:00           0.000000  0.000000e+00         15.0   0.000000   

                       rewards  
time                            
2022-01-01 00:00:00  15.000000  
2022-01-01 00:15:00  15.000000  
2022-01-01 00:30:00  15.000000  
2022-01-01 00:45:00  15.000000  
2022-01-01 01:00:00  15.000000  
...                        ...  
2022-06-06 04:45:00  78.234473  
2022-06-06 05:00:00  15.000000  
2022-06-06 05:15:00  15.000000  
2022-06-06 05:30:00  15.000000  
20

In [27]:
env.plot_VPP_autarky()

In [28]:
#env.plot_Elvis_results()

In [29]:
#env.plot_VPP_results()

In [30]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [31]:
env.plot_VPP_Elvis_comparison()

In [32]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [33]:
env.plot_rewards_stats()

In [34]:
env.plot_EVs_kpi()

In [35]:
env.plot_load_kpi()

In [36]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Validating dataset VPP Simulation using the loaded trained model

In [37]:
#VALIDATING Environment initialization
env = VPPEnv(VPP_validating_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 6261, Arrival time: 2022-01-01 11:45:00, Parking_time: 24, Leaving_time: 2022-01-02 11:45:00, SOC: 0.31751302405828397, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 7825, Arrival time: 2022-12-31 22:00:00, Parking_time: 24, Leaving_time: 2023-01-01 22:00:00, SOC: 0.5736264708599452, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -30085.39 , Grid_used_en(grid-import)=2136.67kWh , autarky-rate=89.6 , RE-to-vehicle_unused_en(grid-export)=-32222.06kWh , self-consump.rate=36.4 , Total_selling_cost=€  -1187.15 , Grid_cost=€  113.34
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  22043.72 , Grid_used_en=kWh  42981.83 , RE-to-vehicle_unused_en=kWh  20938.11 , Total_selling_cost=€  1015.52 , Grid_cost=€  1864.05 , Charging_events=  1565 
- Exp.VPP_goals: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  70.59


In [38]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
#env.plot_VPP_input_data()

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  22581.19 , Grid_used_en(grid-import)=42150.88kWh , Total_demand=73232.88kWh , autarky-rate=42.4 , RE-to-vehicle_unused_en(grid-export)=19569.69kWh , Total_supply=50651.69kWh , self-consump.rate=61.4 , Grid_cost=€  1822.55 , Total_selling_cost=€  1023.72 , Av.EV_en_left=kWh  100.0 , Charging_events=  1565 
- VPP_goal_upper_limit: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  70.59
Simulating VPP....


In [39]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



In [40]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  22330.82 , Grid_used_en(grid-import)=42823.75kWh , Total_demand=72938.36kWh , autarky-rate=41.3 , RE-to-vehicle_unused_en(grid-export)=20492.93kWh , Total_supply=50607.53kWh , self-consump.rate=59.5 , Grid_cost=€  1874.93 , Total_selling_cost=€  1042.89 , Av.EV_en_left=kWh  100.0 , Charging_events=  1565 
- VPP_goal_upper_limit: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  70.59
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -3378.02 , Grid_used_en(grid-import)=630.83kWh , Total_demand=59912.83kWh , autarky-rate=98.9 , RE-to-vehicle_unused_en(grid-export)=4008.85kWh , Total_supply=63290.85kWh , self-consump.rate=93.7 , Total_selling_cost=€  -112.59 , Grid_cost=€  29.21 
 EV_INFO: Av.EV_energy_leaving=kWh  67.18 , Std.EV_energy_leaving=kWh  23.43 , EV_departures =  1563 , EV_queue_left =  0
SCORE:  Cumulative_reward= 508020.16 - Step_rewars (load_t= 433972.34, EVs_

In [41]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [42]:
VPP_table.head(15000)

0          1          2    3  \
time                                                        
2022-01-01 00:00:00   0.000000   0.000000   0.000000  0.0   
2022-01-01 00:15:00   0.000000   0.000000   0.000000  0.0   
2022-01-01 00:30:00   0.000000   0.000000   0.000000  0.0   
2022-01-01 00:45:00   0.000000   0.000000   0.000000  0.0   
2022-01-01 01:00:00   0.000000   0.000000   0.000000  0.0   
...                        ...        ...        ...  ...   
2022-06-06 04:45:00  61.985752  63.149704  70.315170  0.0   
2022-06-06 05:00:00  63.661125  63.149704  71.990547  0.0   
2022-06-06 05:15:00  65.428276  63.149704  73.757698  0.0   
2022-06-06 05:30:00  67.251663  63.149704  75.581085  0.0   
2022-06-06 05:45:00  68.881912  63.149704  77.211334  0.0   

                                       EVs_id       actions  \
time                                                          
2022-01-01 00:00:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:15:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:30:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:45:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 01:00:00              [0, 0, 0, 0]  [2, 0, 1, 0]   
...                                       ...           ...   
2022-06-06 04:45:00  [10068, 10066, 10067, 0]  [1, 0, 1, 2]   
2022-06-06 05:00:00  [10068, 10066, 10067, 0]  [1, 0, 1, 2]   
2022-06-06 05:15:00  [10068, 10066, 10067, 0]  [1, 0, 1, 0]   
2022-06-06 05:30:00  [10068, 10066, 10067, 0]  [1, 0, 1, 0]   
2022-06-06 05:45:00  [10068, 10066, 10067, 0]  [1, 0, 1, 0]   

                                      mask_truth  ev_charged_pwr  \
time                                                               
2022-01-01 00:00:00  [False, False, False, True]        0.000000   
2022-01-01 00:15:00  [False, False, False, True]        0.000000   
2022-01-01 00:30:00  [False, False, False, True]        0.000000   
2022-01-01 00:45:00  [False, False, False, True]        0.000000   
2022-01-01 01:00:00   [False, True, False, True]        0.000000   
...                                          ...             ...   
2022-06-06 04:45:00    [True, True, True, False]       10.361534   
2022-06-06 05:00:00   [True, False, True, False]       13.402989   
2022-06-06 05:15:00    [True, False, True, True]       14.137229   
2022-06-06 05:30:00    [True, False, True, True]       14.587074   
2022-06-06 05:45:00    [True, False, True, True]       13.041997   

                     ev_discharged_pwr      load  load_reward  EV_reward  \
time                                                                       
2022-01-01 00:00:00                0.0 -3.922208    -4.337643        0.0   
2022-01-01 00:15:00                0.0 -3.602586    -5.809085        0.0   
2022-01-01 00:30:00                0.0 -4.889993    -2.433117        0.0   
2022-01-01 00:45:00                0.0 -2.459870    -4.925831        0.0   
2022-01-01 01:00:00                0.0 -3.955498    -4.902986        0.0   
...                                ...       ...          ...        ...   
2022-06-06 04:45:00                0.0  0.000000    15.000000        0.0   
2022-06-06 05:00:00                0.0  0.000000    15.000000        0.0   
2022-06-06 05:15:00                0.0  0.000000    15.000000        0.0   
2022-06-06 05:30:00                0.0  0.000000    15.000000        0.0   
2022-06-06 05:45:00                0.0  0.000000    15.000000        0.0   

                       rewards  
time                            
2022-01-01 00:00:00  -4.337643  
2022-01-01 00:15:00  -5.809085  
2022-01-01 00:30:00  -2.433117  
2022-01-01 00:45:00  -4.925831  
2022-01-01 01:00:00  -4.902986  
...                        ...  
2022-06-06 04:45:00  15.000000  
2022-06-06 05:00:00  15.000000  
2022-06-06 05:15:00  15.000000  
2022-06-06 05:30:00  15.000000  
2022-06-06 05:45:00  15.000000  

[15000 rows x 13 columns]

In [43]:
env.plot_VPP_autarky()

In [44]:
#env.plot_VPP_results()


In [45]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [46]:
env.plot_VPP_Elvis_comparison()

In [47]:
env.plot_rewards_results()

In [48]:
env.plot_rewards_stats()

In [49]:
env.plot_EVs_kpi()

In [50]:
env.plot_load_kpi()

In [51]:
env.plot_yearly_load_log()

## Training dataset VPP Simulation using the loaded trained model

In [52]:
#TRAINING Environment initialization
env = VPPEnv(VPP_training_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 10956, Arrival time: 2022-01-01 13:00:00, Parking_time: 23.47859970983158, Leaving_time: 2022-01-02 12:28:42.958955, SOC: 0.48308014621006795, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 12520, Arrival time: 2022-12-31 13:45:00, Parking_time: 24, Leaving_time: 2023-01-01 13:45:00, SOC: 0.6045231408464643, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -34117.7 , Grid_used_en(grid-import)=1556.25kWh , autarky-rate=90.5 , RE-to-vehicle_unused_en(grid-export)=-35673.95kWh , self-consump.rate=29.4 , Total_selling_cost=€  -1196.64 , Grid_cost=€  97.86
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  17894.27 , Grid_used_en=kWh  39678.77 , RE-to-vehicle_unused_en=kWh  21784.5 , Total_selling_cost=€  866.11 , Grid_cost=€  1663.4 , Charging_events=  1565 
- Exp.VPP_goals: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  72.79


In [53]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
#env.plot_VPP_input_data()

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  18561.42 , Grid_used_en(grid-import)=40163.2kWh , Total_demand=69068.44kWh , autarky-rate=41.9 , RE-to-vehicle_unused_en(grid-export)=21601.79kWh , Total_supply=50507.03kWh , self-consump.rate=57.2 , Grid_cost=€  1670.53 , Total_selling_cost=€  887.53 , Av.EV_en_left=kWh  100.0 , Charging_events=  1565 
- VPP_goal_upper_limit: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  72.79
Simulating VPP....


In [54]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



In [55]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  18527.34 , Grid_used_en(grid-import)=39418.85kWh , Total_demand=69008.81kWh , autarky-rate=42.9 , RE-to-vehicle_unused_en(grid-export)=20891.51kWh , Total_supply=50481.47kWh , self-consump.rate=58.6 , Grid_cost=€  1634.6 , Total_selling_cost=€  857.58 , Av.EV_en_left=kWh  100.0 , Charging_events=  1565 
- VPP_goal_upper_limit: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  72.79
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -4415.84 , Grid_used_en(grid-import)=640.02kWh , Total_demand=57979.07kWh , autarky-rate=98.9 , RE-to-vehicle_unused_en(grid-export)=5055.86kWh , Total_supply=62394.91kWh , self-consump.rate=91.9 , Total_selling_cost=€  -148.71 , Grid_cost=€  24.76 
 EV_INFO: Av.EV_energy_leaving=kWh  68.97 , Std.EV_energy_leaving=kWh  23.54 , EV_departures =  1561 , EV_queue_left =  0
SCORE:  Cumulative_reward= 492017.02 - Step_rewars (load_t= 412759.31, EVs_en

In [56]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [57]:
VPP_table.head(14995)

0          1          2    3  \
time                                                        
2022-01-01 00:00:00   0.000000   0.000000   0.000000  0.0   
2022-01-01 00:15:00   0.000000   0.000000   0.000000  0.0   
2022-01-01 00:30:00   0.000000   0.000000   0.000000  0.0   
2022-01-01 00:45:00   0.000000   0.000000   0.000000  0.0   
2022-01-01 01:00:00   0.000000   0.000000   0.000000  0.0   
...                        ...        ...        ...  ...   
2022-06-06 03:30:00  80.956650  89.651474  35.930058  0.0   
2022-06-06 03:45:00  81.562157  90.256981  35.680058  0.0   
2022-06-06 04:00:00  82.496429  91.191254  35.430058  0.0   
2022-06-06 04:15:00  83.371315  90.941254  36.304943  0.0   
2022-06-06 04:30:00  84.298775  90.691254  37.232399  0.0   

                                       EVs_id       actions  \
time                                                          
2022-01-01 00:00:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:15:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:30:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:45:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 01:00:00              [0, 0, 0, 0]  [2, 0, 1, 0]   
...                                       ...           ...   
2022-06-06 03:30:00  [14754, 14753, 14755, 0]  [1, 1, 2, 2]   
2022-06-06 03:45:00  [14754, 14753, 14755, 0]  [1, 1, 2, 2]   
2022-06-06 04:00:00  [14754, 14753, 14755, 0]  [1, 2, 1, 2]   
2022-06-06 04:15:00  [14754, 14753, 14755, 0]  [1, 2, 1, 2]   
2022-06-06 04:30:00  [14754, 14753, 14755, 0]  [1, 2, 1, 2]   

                                      mask_truth  ev_charged_pwr  \
time                                                               
2022-01-01 00:00:00  [False, False, False, True]        0.000000   
2022-01-01 00:15:00  [False, False, False, True]        0.000000   
2022-01-01 00:30:00  [False, False, False, True]        0.000000   
2022-01-01 00:45:00  [False, False, False, True]        0.000000   
2022-01-01 01:00:00   [False, True, False, True]        0.000000   
...                                          ...             ...   
2022-06-06 03:30:00   [True, True, False, False]        5.980636   
2022-06-06 03:45:00   [True, True, False, False]        4.844085   
2022-06-06 04:00:00   [True, False, True, False]        7.474210   
2022-06-06 04:15:00   [True, False, True, False]        6.999086   
2022-06-06 04:30:00   [True, False, True, False]        7.419662   

                     ev_discharged_pwr          load  load_reward  EV_reward  \
time                                                                           
2022-01-01 00:00:00                0.0 -3.734929e+00    -2.721928        0.0   
2022-01-01 00:15:00                0.0 -2.633157e+00    -3.687950        0.0   
2022-01-01 00:30:00                0.0 -3.212770e+00    -3.375710        0.0   
2022-01-01 00:45:00                0.0 -3.025426e+00    -6.070449        0.0   
2022-01-01 01:00:00                0.0 -5.177494e+00    -5.782245        0.0   
...                                ...           ...          ...        ...   
2022-06-06 03:30:00               -1.0  0.000000e+00    15.000000        0.0   
2022-06-06 03:45:00               -1.0  4.440892e-16    15.000000        0.0   
2022-06-06 04:00:00               -1.0  0.000000e+00    15.000000        0.0   
2022-06-06 04:15:00               -1.0  0.000000e+00    15.000000        0.0   
2022-06-06 04:30:00               -1.0  0.000000e+00    15.000000        0.0   

                       rewards  
time                            
2022-01-01 00:00:00  -2.721928  
2022-01-01 00:15:00  -3.687950  
2022-01-01 00:30:00  -3.375710  
2022-01-01 00:45:00  -6.070449  
2022-01-01 01:00:00  -5.782245  
...                        ...  
2022-06-06 03:30:00  15.000000  
2022-06-06 03:45:00  15.000000  
2022-06-06 04:00:00  15.000000  
2022-06-06 04:15:00  15.000000  
2022-06-06 04:30:00  15.000000  

[14995 rows x 13 columns]

In [58]:
env.plot_VPP_autarky()

In [59]:
#env.plot_VPP_results()

In [60]:
env.plot_VPP_supply_demand()

In [61]:
env.plot_VPP_Elvis_comparison()

In [62]:
env.plot_rewards_results()

In [63]:
env.plot_rewards_stats()

In [64]:
env.plot_EVs_kpi()

In [65]:
env.plot_actions_kpi()

In [66]:
env.plot_load_kpi()

In [67]:
env.plot_yearly_load_log()

In [68]:
#env.close()